In [1]:
# Using all width of the page!
from IPython.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

from datetime import datetime, date
import matplotlib.pyplot as plt
from pandas.plotting import register_matplotlib_converters
register_matplotlib_converters()
import pandas as pd

from jesse import research, utils
import jesse.indicators as ta
import custom_indicators as cta
from strategies.BottinoLib import utils as bu
import numpy as np

!pip install --upgrade mplfinance
from mplfinance.original_flavor import candlestick_ohlc
from matplotlib.dates import HourLocator, MonthLocator, YearLocator

import matplotlib.dates as mdates
import matplotlib.ticker as mticker

import lightweight as lw

TIMESTAMP = 0
OPEN = 1
CLOSE = 2
HIGH = 3
LOW = 4
VOLUME = 5

WARMUP_INDICATOR_LENGTH = 50

def lines_to_df(cols_array, data_series, time_series, col_time = "time"):
    df = pd.DataFrame(data=data_series, index=time_series, columns=cols_array)
    df[col_time] = pd.to_datetime(df.index, unit="ms")
    return df

In [2]:
# User Input : -------

# Window time interval
date_start = date(2021, 6, 1)
date_end = date(2021, 7, 15)

exchange = 'FTX Futures'
pair = 'BTC-USD'

# --------------------

days_range = (date_end-date_start).days
print(f'days range: {days_range}')

TIME_RANGE_START = date_start.strftime("%Y-%m-%d")
TIME_RANGE_END = date_end.strftime("%Y-%m-%d")

CHART_SIZE_WIDTH_INCH_PER_DAY = 10
CHART_SIZE_WIDTH = CHART_SIZE_WIDTH_INCH_PER_DAY * days_range
CHART_SIZE_HEIGH = 18

# Getting candles data from Exchange
btc_candles = research.get_candles(exchange, pair, '5m', TIME_RANGE_START, TIME_RANGE_END)
btc_anchor_candles = research.get_candles(exchange, pair, '1h', TIME_RANGE_START, TIME_RANGE_END)

# Indicators
ema_50 = ta.ema(btc_candles, 50, sequential=True)
MAMA_FAST_LIMIT = 0.13
MAMA_SLOW_LIMIT = 0.06
mf = ta.mama(btc_candles, fastlimit=MAMA_FAST_LIMIT, slowlimit=MAMA_SLOW_LIMIT, sequential=True)
# Indicators Anchor Timeframe (optional)
a_ema_50 = ta.ema(btc_anchor_candles, 50, sequential=True)
a_ema_200 = ta.ema(btc_anchor_candles, 200, sequential=True)

# Adjusting timestamp for Pandas DataFrame
times = []
for c in btc_candles:
    times.append(datetime.fromtimestamp(c[0] / 1000))
times_anchor = []
for c in btc_anchor_candles:
    times_anchor.append(datetime.fromtimestamp(c[0] / 1000))

df_candles = utils.numpy_candles_to_dataframe(btc_candles)
a_df_candles = utils.numpy_candles_to_dataframe(btc_anchor_candles)
df_candles["time"] = pd.to_datetime(df_candles["date"]).astype(int) // 10**9
a_df_candles["time"] = pd.to_datetime(a_df_candles['date']).astype(int) // 10**9

# Removing first data of some indicators, at the beginning they are forming and first values can be far from price
a_t = times_anchor[WARMUP_INDICATOR_LENGTH:]
a_ema = a_ema_50[WARMUP_INDICATOR_LENGTH:]
a_emaslow = a_ema_200[WARMUP_INDICATOR_LENGTH:]
t = times[WARMUP_INDICATOR_LENGTH:]
fama = mf.fama[WARMUP_INDICATOR_LENGTH:]
ema = ema_50[WARMUP_INDICATOR_LENGTH:]
columns = ['time', 'fama', 'ema']
a_columns = ['time', 'a_ema', 'a_emaslow']
data_series = np.dstack((t, fama, ema))
a_data_series = np.dstack((a_t, a_ema, a_emaslow))
data_series = np.squeeze(data_series, axis=0)
a_data_series = np.squeeze(a_data_series, axis=0)
df_indicators = lines_to_df(columns, data_series, t)
a_df_indicators = lines_to_df(a_columns, a_data_series, a_t)
df_indicators["time"] = df_candles["time"][WARMUP_INDICATOR_LENGTH:]
a_df_indicators["time"] = a_df_candles["time"][WARMUP_INDICATOR_LENGTH:]

lw.plot(
    df_candles,
    data=df_indicators[columns],
    data_anchor=a_df_indicators[a_columns], # optional
    config=[
        {'name': 'fama', 'fn': 'addLineSeries', 'style': {'color': '#01A781', 'lineWidth': 1}},
        {'name': 'ema', 'fn': 'addLineSeries', 'style': {'color': '#CC0BA1', 'lineWidth': 2}},
    ],
    config_anchor=[
        {'name': 'a_ema', 'fn': 'addLineSeries', 'style': {'color': 'yellow', 'lineWidth': 1}},
        {'name': 'a_emaslow', 'fn': 'addLineSeries', 'style': {'color': '#1EACF8', 'lineWidth': 2}},
    ],  # optional
    dark_theme=True, # optional
    width=1900, height=850 # optional
)

days range: 44


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [21]:
# Example Chart with just higher timeframe candles and indicators
lw.plot(
    a_df_candles,
    data=a_df_indicators[a_columns],
    config=[
        {'name': 'a_ema', 'fn': 'addLineSeries', 'style': {'color': 'yellow', 'lineWidth': 1}},
        {'name': 'a_emaslow', 'fn': 'addLineSeries', 'style': {'color': '#1EACF8', 'lineWidth': 2}},
    ],
    dark_theme=True, # optional
    width=1900, height=850 # optional
)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>